In [1]:
import fasttext
import pandas as pd
import re

In [2]:
filepath = 'data.xlsx'

data = pd.read_excel(filepath)

In [3]:
data.head(5)

Numéro d'application Date d'application  Numero de publication  \
0              17167919         2017-04-25                3264223   
1              17166775         2017-04-18                3235458   
2              17166069         2017-04-11                3249094   
3              18771363         2018-03-05                3605724   
4              19881950         2019-11-01                3713245   

  date de publication                                                CPC  \
0          2018-01-03  ['B23K26-361', 'H04M1-0266', 'B23K26-402', 'G0...   
1          2017-10-25  ['A61B17-68', 'A61B17-888', 'A61B17-8685', 'A6...   
2          2017-11-29                        ['D06F58-206', 'D06F58-20']   
3          2020-02-05  ['H01P1-2138', 'H01P5-107', 'H01P1-2088', 'H01...   
4          2020-09-23      ['H04N21-4345', 'H04N21-4821', 'H04N21-4316']   

                                                 IPC  \
0  ['C08J7-04', 'H04M1-02', 'G06F1-16', 'B23K26-3...   
1            ['A61B17-88', 'A61B17-68', 'A61B17-86']   
2                         ['D06F58-20', 'D06F58-02']   
3             ['H01P3-12', 'H01P1-213', 'H01P5-107']   
4                       ['H04N21-482', 'H04N21-262']   

                                               claim  \
0  <!-- EPO <DP n="18"> --><claim id="c-en-0001" ...   
1  <!-- EPO <DP n="20"> --><claim id="c-en-0001" ...   
2  <!-- EPO <DP n="22"> --><claim id="c-en-0001" ...   
3  <!-- EPO <DP n="62"> --><claim id="c-en-0001" ...   
4  <!-- EPO <DP n="14"> --><claim id="c-en-0001" ...   

                                         description  
0  <!-- EPO <DP n="1"> --><p id="p0001" num="0001...  
1  <!-- EPO <DP n="1"> --><heading id="h0001">FIE...  
2  <!-- EPO <DP n="1"> --><heading id="h0001"><b>...  
3  <!-- EPO <DP n="1"> --><heading id="h0001">Tec...  
4  <!-- EPO <DP n="1"> --><p id="p0001" num="0001...

In [4]:
import re
import ast
from collections import Counter

def split_code(l):

    # Cette fonction prend une liste de codes alphanumériques et retourne une nouvelle liste
    # contenant les sections les plus fréquentes à chaque position, tout en respectant
    # la validité des sélections précédentes pour maintenir la correspondance avec les codes originaux.
    
    l = ast.literal_eval(l)
    splitted_code_list = []
    splitted_code = []

    # Diviser chaque code et séparer les lettres et les chiffres
    for elt in l:
        elt = elt.split('-')
        letters = list(filter(None, re.split(r'[0-9]', elt[0])))
        digits = list(filter(None, re.split(r'[A-Z]', elt[0])))
        code = [sub[item] for item in range(len(digits)) for sub in [letters, digits]]
        code.append(elt[1])
        splitted_code.append(code)

    # Déterminer les sections les plus prédominantes tout en maintenant la validité
    result = []
    filtered_codes = splitted_code

    for i in range(len(splitted_code[0])):
        # Extraire les éléments ièmes des codes filtrés
        ith_elements = [code[i] for code in filtered_codes]
        
        # Trouver l'élément le plus commun
        most_common, _ = Counter(ith_elements).most_common(1)[0]
        
        # Ajouter l'élément le plus commun au résultat
        result.append(most_common)
        
        # Filtrer les codes pour la prochaine itération
        filtered_codes = [code for code in filtered_codes if code[i] == most_common]

    # We add a the concatenated code to the result
    #result.append('-'.join(result[0:3]) + '-' + result[3])

    return result

# Exemple d'utilisation
res = split_code("['B23K26-361', 'H04C1-0266', 'B23K26-402', 'M04C1-0256', 'U04C1-0246']")
print(res)

['B', '23', 'K', '26', '361']


In [5]:
cpc_cleaned = data['CPC'].apply(split_code).apply(pd.Series)
cpc_cleaned.columns = ['CPC_section','CPC_class','CPC_subclass','CPC_group','CPC_subgroup']

# We add the columns to the original dataframe
data = pd.concat([data, cpc_cleaned], axis=1)

data.drop(['Numéro d\'application', 'Date d\'application','Numero de publication', 'date de publication'], axis=1, inplace=True)

data.head()

CPC  \
0  ['B23K26-361', 'H04M1-0266', 'B23K26-402', 'G0...   
1  ['A61B17-68', 'A61B17-888', 'A61B17-8685', 'A6...   
2                        ['D06F58-206', 'D06F58-20']   
3  ['H01P1-2138', 'H01P5-107', 'H01P1-2088', 'H01...   
4      ['H04N21-4345', 'H04N21-4821', 'H04N21-4316']   

                                                 IPC  \
0  ['C08J7-04', 'H04M1-02', 'G06F1-16', 'B23K26-3...   
1            ['A61B17-88', 'A61B17-68', 'A61B17-86']   
2                         ['D06F58-20', 'D06F58-02']   
3             ['H01P3-12', 'H01P1-213', 'H01P5-107']   
4                       ['H04N21-482', 'H04N21-262']   

                                               claim  \
0  <!-- EPO <DP n="18"> --><claim id="c-en-0001" ...   
1  <!-- EPO <DP n="20"> --><claim id="c-en-0001" ...   
2  <!-- EPO <DP n="22"> --><claim id="c-en-0001" ...   
3  <!-- EPO <DP n="62"> --><claim id="c-en-0001" ...   
4  <!-- EPO <DP n="14"> --><claim id="c-en-0001" ...   

                                         description CPC_section CPC_class  \
0  <!-- EPO <DP n="1"> --><p id="p0001" num="0001...           B        23   
1  <!-- EPO <DP n="1"> --><heading id="h0001">FIE...           A        61   
2  <!-- EPO <DP n="1"> --><heading id="h0001"><b>...           D        06   
3  <!-- EPO <DP n="1"> --><heading id="h0001">Tec...           H        01   
4  <!-- EPO <DP n="1"> --><p id="p0001" num="0001...           H        04   

  CPC_subclass CPC_group CPC_subgroup  
0            K        26          361  
1            B        17           68  
2            F        58          206  
3            P         1         2138  
4            N        21         4345

In [6]:
import re
import nltk
import string
from nltk.corpus import stopwords

nltk.download('stopwords')

def clean_text(text):
    # Remove HTML tags
    text = re.sub('<.*?>', ' ', text)
    
    # Remove specific patterns (e.g., '-->')
    text = re.sub('-->', '', text)
    
    # Remove punctuation
    translator = str.maketrans('', '', string.punctuation)
    text = text.translate(translator)
    
    # Convert to lowercase
    text = text.lower()
    
    # Remove numbers
    text = re.sub(r'[0-9]', '', text)
    
    # Remove extra whitespace
    text = " ".join(text.split())
    
    # Remove stopwords
    stop_words = set(stopwords.words('english'))
    words = text.split()
    filtered_words = [word for word in words if word.lower() not in stop_words]
    text = ' '.join(filtered_words)
    
    return text


[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/youssouf/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [7]:
data['description'] = data['description'] + ' ' + data['claim']
data['description'] = data['description'].apply(clean_text)

data.drop(['claim'], axis=1, inplace=True)

In [8]:
data.head(1)

CPC  \
0  ['B23K26-361', 'H04M1-0266', 'B23K26-402', 'G0...   

                                                 IPC  \
0  ['C08J7-04', 'H04M1-02', 'G06F1-16', 'B23K26-3...   

                                         description CPC_section CPC_class  \
0  present invention relates cover window display...           B        23   

  CPC_subclass CPC_group CPC_subgroup  
0            K        26          361

In [42]:
# We split the dataframe into training and testing sets
from sklearn.model_selection import train_test_split

train, test = train_test_split(data, test_size=0.2, random_state=42)

In [11]:
import os
import pandas as pd

def generate_fasttext_files(data):
    """
    Main function to generate FastText format files for hierarchical classification.
    """
    # Create a main directory to store the FastText files
    output_dir = "fasttext_files"
    os.makedirs(output_dir, exist_ok=True)

    # Step 1: Generate FastText file for CPC section
    section_dir = os.path.join(output_dir, "sections")
    os.makedirs(section_dir, exist_ok=True)
    create_fasttext_file(data, "CPC_section", os.path.join(section_dir, "fasttext_section.txt"))

    # Get unique CPC sections
    unique_sections = data["CPC_section"].unique()

    # Step 2: For each section, generate FastText file for CPC class
    for section in unique_sections:
        filtered_data = filter_data(data, "CPC_section", section)
        class_dir = os.path.join(section_dir, f"section_{section}")
        os.makedirs(class_dir, exist_ok=True)
        output_file = os.path.join(class_dir, f"fasttext_section_{section}_class.txt")
        create_fasttext_file(filtered_data, "CPC_class", output_file)

        # Get unique CPC classes within this section
        unique_classes = filtered_data["CPC_class"].unique()

        # Step 3: For each class, generate FastText file for CPC subclass
        for cpc_class in unique_classes:
            filtered_data_class = filter_data(filtered_data, "CPC_class", cpc_class)
            subclass_dir = os.path.join(class_dir, f"class_{cpc_class}")
            os.makedirs(subclass_dir, exist_ok=True)
            output_file = os.path.join(subclass_dir, f"fasttext_section_{section}_class_{cpc_class}_subclass.txt")
            create_fasttext_file(filtered_data_class, "CPC_subclass", output_file)

            # Get unique CPC subclasses within this class
            unique_subclasses = filtered_data_class["CPC_subclass"].unique()

            # Step 4: For each subclass, generate FastText file for CPC group
            for subclass in unique_subclasses:
                filtered_data_subclass = filter_data(filtered_data_class, "CPC_subclass", subclass)
                group_dir = os.path.join(subclass_dir, f"subclass_{subclass}")
                os.makedirs(group_dir, exist_ok=True)
                output_file = os.path.join(group_dir, f"fasttext_section_{section}_class_{cpc_class}_subclass_{subclass}_group.txt")
                create_fasttext_file(filtered_data_subclass, "CPC_group", output_file)

                # Get unique CPC groups within this subclass
                unique_groups = filtered_data_subclass["CPC_group"].unique()

                # Step 5: For each group, generate FastText file for CPC subgroup
                for group in unique_groups:
                    filtered_data_group = filter_data(filtered_data_subclass, "CPC_group", group)
                    subgroup_dir = os.path.join(group_dir, f"group_{group}")
                    os.makedirs(subgroup_dir, exist_ok=True)
                    output_file = os.path.join(subgroup_dir, f"fasttext_section_{section}_class_{cpc_class}_subclass_{subclass}_group_{group}_subgroup.txt")
                    create_fasttext_file(filtered_data_group, "CPC_subgroup", output_file)

def create_fasttext_file(data, target_column, output_file):
    """
    Creates a FastText formatted file for the given target column and saves it to the specified output file.
    """
    with open(output_file, 'w') as file:
        for index, row in data.iterrows():
            text = row['description']
            label = row[target_column]
            file.write(f"__label__{label} {text}\n")

def filter_data(data, filter_column, filter_value):
    """
    Filters the dataframe based on the specified column and value.
    """
    return data[data[filter_column] == filter_value]

In [12]:

generate_fasttext_files(train)  # We generate the FastText files for the training set

In [14]:
import os
import fasttext

def train_fasttext_models(base_dir):
    """
    Train FastText models for each hierarchical level.
    """
    # Step 1: Train model for CPC section
    section_file = os.path.join(base_dir, "sections", "fasttext_section.txt")
    section_model = fasttext.train_supervised(input=section_file)
    section_model.save_model(os.path.join("fasttext_files/sections", "section_model.bin"))

    # Get subfolders for sections
    section_dirs = [d for d in os.listdir(os.path.join(base_dir, "sections")) if os.path.isdir(os.path.join(base_dir, "sections", d))]

    # Step 2: Train model for each CPC class
    for section_dir in section_dirs:
        class_file = os.path.join(base_dir, "sections", section_dir, f"fasttext_{section_dir}_class.txt")
        class_model = fasttext.train_supervised(input=class_file)
        class_model.save_model(os.path.join(base_dir, "sections", section_dir, "class_model.bin"))

        # Get subfolders for classes
        class_dirs = [d for d in os.listdir(os.path.join(base_dir, "sections", section_dir)) if os.path.isdir(os.path.join(base_dir, "sections", section_dir, d))]

        # Step 3: Train model for each CPC subclass
        for class_dir in class_dirs:
            subclass_file = os.path.join(base_dir, "sections", section_dir, class_dir, f"fasttext_{section_dir}_{class_dir}_subclass.txt")
            subclass_model = fasttext.train_supervised(input=subclass_file)
            subclass_model.save_model(os.path.join(base_dir, "sections", section_dir, class_dir, "subclass_model.bin"))

            # Get subfolders for subclasses
            subclass_dirs = [d for d in os.listdir(os.path.join(base_dir, "sections", section_dir, class_dir)) if os.path.isdir(os.path.join(base_dir, "sections", section_dir, class_dir, d))]

            # Step 4: Train model for each CPC group
            for subclass_dir in subclass_dirs:
                group_file = os.path.join(base_dir, "sections", section_dir, class_dir, subclass_dir, f"fasttext_{section_dir}_{class_dir}_{subclass_dir}_group.txt")
                group_model = fasttext.train_supervised(input=group_file)
                group_model.save_model(os.path.join(base_dir, "sections", section_dir, class_dir, subclass_dir, "group_model.bin"))

                # Get subfolders for groups
                group_dirs = [d for d in os.listdir(os.path.join(base_dir, "sections", section_dir, class_dir, subclass_dir)) if os.path.isdir(os.path.join(base_dir, "sections", section_dir, class_dir, subclass_dir, d))]

                # Step 5: Train model for each CPC subgroup
                for group_dir in group_dirs:
                    subgroup_file = os.path.join(base_dir, "sections", section_dir, class_dir, subclass_dir, group_dir, f"fasttext_{section_dir}_{class_dir}_{subclass_dir}_{group_dir}_subgroup.txt")
                    subgroup_model = fasttext.train_supervised(input=subgroup_file)
                    subgroup_model.save_model(os.path.join(base_dir, "sections", section_dir, class_dir, subclass_dir, group_dir, "subgroup_model.bin"))


In [15]:
# Base directory where the FastText files are stored
base_dir = "fasttext_files"

# Train the FastText models
train_fasttext_models(base_dir)

Read 117M words
Number of words:  395771
Number of labels: 9
Progress: 100.0% words/sec/thread: 8141170 lr:  0.000000 avg.loss:  0.925288 ETA:   0h 0m 0s
Read 10M words
Number of words:  45559
Number of labels: 18
Progress: 100.0% words/sec/thread: 7557528 lr:  0.000000 avg.loss:  2.536731 ETA:   0h 0m 0s
Read 0M words
Number of words:  7328
Number of labels: 5
Progress: 100.0% words/sec/thread: 1111624 lr:  0.000000 avg.loss:  1.613351 ETA:   0h 0m 0s
Read 0M words
Number of words:  2085
Number of labels: 5
Progress: 100.0% words/sec/thread:  102712 lr:  0.000000 avg.loss:  1.613352 ETA:   0h 0m 0s
Read 0M words
Number of words:  952
Number of labels: 2
Progress: 100.0% words/sec/thread:   44114 lr:  0.000000 avg.loss:  0.695104 ETA:   0h 0m 0s
Read 0M words
Number of words:  516
Number of labels: 1
Progress: 100.0% words/sec/thread:   30632 lr:  0.000000 avg.loss:  0.000000 ETA:   0h 0m 0s
Read 0M words
Number of words:  606
Number of labels: 1
Progress: 100.0% words/sec/thread:   44

In [10]:
data['description'][1]

'field invention present disclosure relates implantable screws particularly disclosure relates implantable screws configured provide compression upon bone screw implanted background invention broken bone must carefully stabilized supported strong enough handle bodys weight movement last century physicians relied casts splints support stabilize bone outside body advent sterile surgical procedures reduced risk infection allowing doctors internally set stabilize fractured bones surgical procedure set fracture bone fragments first repositioned reduced normal alignment held together special implants plates screws nails wires screws used internal fixation often type implant although screw simple device different designs based type fracture screw used screws come different sizes use bones different sizes screws used alone hold fracture well plates rods nails bone heals screws may either left place removed many instances desired inserted screw provide compression bone joint fracture line reduc

In [11]:
data[['CPC_section','CPC_class','CPC_subclass','CPC_group','CPC_subgroup']]

CPC_section CPC_class CPC_subclass CPC_group CPC_subgroup
0               B        23            K        26          361
1               A        61            B        17           68
2               D        06            F        58          206
3               H        01            P         1         2138
4               H        04            N        21         4345
...           ...       ...          ...       ...          ...
49995           A        61            K      2800           95
49996           B        60            R         7           02
49997           C        07            K      2317           21
49998           G        07            F        11           62
49999           B        01            F        23          235

[50000 rows x 5 columns]

In [43]:
import ast
import re

def split_code_mult(l):
    l = ast.literal_eval(l)
    splitted_code_list = []
    splitted_code = []
    # Use sets to store unique elements for each level
    level_sets = [set() for _ in range(5)]
    
    for elt in l:
        elt = elt.split('-')
        letters = list(filter(None, re.split(r'[0-9]', elt[0])))
        digits = list(filter(None, re.split(r'[A-Z]', elt[0])))
        code = [sub[item] for item in range(len(digits))
                           for sub in [letters, digits]]
        code.append(elt[1])
        splitted_code.append(code)
    
    for code in splitted_code:
        for i in range(len(code)):
            level_sets[i].add(code[i])
    
    # Convert sets back to lists
    splitted_code_list = [list(level) for level in level_sets]

    return splitted_code_list

# Example usage
res = split_code_mult("['B23K26-361', 'H04C1-0266', 'B23K26-402', 'M04C1-0256', 'U04C1-0246']")
print(res)


[['M', 'H', 'B', 'U'], ['23', '04'], ['C', 'K'], ['1', '26'], ['0266', '0256', '361', '402', '0246']]


In [45]:
test.head(1)

CPC            IPC  \
33553  ['B60R22-20', 'Y10T24-4084', 'Y10T24-4019']  ['B60R22-20']   

                                             description CPC_section  \
33553  background field invention present invention r...           Y   

      CPC_class CPC_subclass CPC_group CPC_subgroup  
33553        10            T        24         4084

In [50]:
# We split all the cpc codes for each patent into 5 columns
cpc_cleaned = test['CPC'].apply(split_code_mult).apply(pd.Series)

# We change the column content to the new values
test['CPC_section'] = cpc_cleaned[0]
test['CPC_class'] = cpc_cleaned[1]
test['CPC_subclass'] = cpc_cleaned[2]
test['CPC_group'] = cpc_cleaned[3]
test['CPC_subgroup'] = cpc_cleaned[4]

test.reset_index(drop=True, inplace=True)

test.drop(['CPC', 'IPC'], axis=1, inplace=True)



In [51]:
test.head()

CPC  \
0        ['B60R22-20', 'Y10T24-4084', 'Y10T24-4019']   
1  ['G06F3-0488', 'G06F3-0416', 'G06F2203-04808',...   
2                      ['F16L37-088', 'F16L37-0841']   
3             ['H02H3-006', 'H02H7-26', 'H02H3-044']   
4                         ['H04W24-02', 'H04W24-10']   

                           IPC  \
0                ['B60R22-20']   
1  ['G06F3-041', 'G06F3-0488']   
2               ['F16L37-088']   
3     ['H02H3-00', 'H02H7-26']   
4                ['H04W24-02']   

                                         description CPC_section CPC_class  \
0  background field invention present invention r...      [Y, B]  [10, 60]   
1  technical field present invention relates limi...         [G]      [06]   
2  technical field present disclosure relates pip...         [F]      [16]   
3  present invention relates protection systems p...         [H]      [02]   
4  crossreference related application application...         [H]      [04]   

  CPC_subclass  CPC_group                CPC_subgroup  
0       [R, T]   [22, 24]            [4019, 4084, 20]  
1          [F]  [2203, 3]  [04104, 04808, 0416, 0488]  
2          [L]       [37]                 [088, 0841]  
3          [H]     [7, 3]              [044, 006, 26]  
4          [W]       [24]                    [10, 02]

In [21]:
import os

base_dir = "fasttext_files/sections"

def classify_text_hierarchically(text):
    # Function to classify text at each hierarchical level

    def load_and_predict(model_path, text):
        if not os.path.exists(model_path):
            return None, None
        model = fasttext.load_model(model_path)
        predicted_class, probability = model.predict(text)
        return predicted_class[0].split("__label__")[-1], probability[0]

    result = {}
    
    # Level 1: CPC Section
    section_model_path = os.path.join(base_dir, "section_model.bin")
    cpc_section, section_prob = load_and_predict(section_model_path, text)
    if cpc_section is None:
        result['section'] = "Model not found"
        return result

    result['section'] = {
        'code': cpc_section,
        'probability': section_prob
    }
    
    # Level 2: CPC Class
    class_model_path = os.path.join(base_dir, f"section_{cpc_section}", "class_model.bin")
    cpc_class, class_prob = load_and_predict(class_model_path, text)

    if cpc_class is None:
        result['class'] = "Model not found"
        return result

    result['class'] = {'code': cpc_class, 'probability': class_prob}

    # Level 3: CPC Subclass
    subclass_model_path = os.path.join(base_dir, f"section_{cpc_section}", f"class_{cpc_class}", "subclass_model.bin")
    cpc_subclass, subclass_prob = load_and_predict(subclass_model_path, text)
    if cpc_subclass is None:
        result['subclass'] = "Model not found"
        return result

    result['subclass'] = {'code': cpc_subclass, 'probability': subclass_prob}

    # Level 4: CPC Group
    group_model_path = os.path.join(base_dir, f"section_{cpc_section}", f"class_{cpc_class}", f"subclass_{cpc_subclass}", "group_model.bin")
    cpc_group, group_prob = load_and_predict(group_model_path, text)
    if cpc_group is None:
        result['group'] = "Model not found"
        return result

    result['group'] = {'code': cpc_group, 'probability': group_prob}

    # Level 5: CPC Subgroup
    subgroup_model_path = os.path.join(base_dir, f"section_{cpc_section}", f"class_{cpc_class}", f"subclass_{cpc_subclass}", f"group_{cpc_group}", "subgroup_model.bin")
    cpc_subgroup, subgroup_prob = load_and_predict(subgroup_model_path, text)
    if cpc_subgroup is None:
        result['subgroup'] = "Model not found"
        return result

    result['subgroup'] = {'code': cpc_subgroup, 'probability': subgroup_prob}

    # Combine the full CPC code
    result['full_cpc_code'] = f"{cpc_section}{cpc_class}{cpc_subclass}{cpc_group}/{cpc_subgroup}"

    return result

In [128]:
import plotly.graph_objs as go
import plotly.express as px
from prettytable import PrettyTable
import plotly.io as pio

def evaluate_model_multi_label(test_data):
    levels = ['section', 'class', 'subclass', 'group', 'subgroup']
    results = {level: {'tp': 0, 'fp': 0, 'fn': 0} for level in levels}
    
    # On parcourt chaque ligne des données de test
    for idx, row in test_data.iterrows():
        result = classify_text_hierarchically(row['description'])
        
        correct = True
        # On évalue chaque niveau hiérarchique
        for level in levels:
            true_label = row[f'CPC_{level}']
            pred_label = result[level]['code']
            
            if correct:
                if pred_label in true_label:
                    results[level]['tp'] += 1
                else:
                    results[level]['fp'] += 1
                    correct = False
            else:
                results[level]['fn'] += 1

    cumulative_tp = 0
    cumulative_fp = 0
    cumulative_fn = 0
    
    f1_scores = []
    precision_scores = []
    recall_scores = []
    score_table = PrettyTable()

    # On définit les en-têtes du tableau des scores
    score_table.field_names = ["Level", "Precision", "Recall", "F1 Score"]

    # On calcule les scores pour chaque niveau
    for i, level in enumerate(levels):
        cumulative_tp += results[level]['tp']
        cumulative_fp += results[level]['fp']
        cumulative_fn += results[level]['fn']
        
        precision = cumulative_tp / (cumulative_tp + cumulative_fp) if (cumulative_tp + cumulative_fp) > 0 else 0
        recall = cumulative_tp / (cumulative_tp + cumulative_fn) if (cumulative_tp + cumulative_fn) > 0 else 0
        f1 = 2 * (precision * recall) / (precision + recall) if (precision + recall) > 0 else 0
        
        f1_scores.append(f1)
        precision_scores.append(precision)
        recall_scores.append(recall)
        
        # On ajoute les scores au tableau
        score_table.add_row([level.capitalize(), round(precision, 2), round(recall, 2), round(f1, 2)])

    # On affiche les scores sous forme de tableau en utilisant PrettyTable
    print(score_table)

    # On génère et affiche le graphique interactif des scores
    plot_interactive_f1_scores(levels, f1_scores, precision_scores, recall_scores)

def plot_interactive_f1_scores(levels, f1_scores, precision_scores, recall_scores):
    # On crée un DataFrame pour les scores
    df = pd.DataFrame({
        'Levels': levels,
        'F1 Score': f1_scores,
        'Precision': precision_scores,
        'Recall': recall_scores
    })
    
    # On crée des graphiques interactifs en utilisant plotly
    fig = go.Figure()
    
    # On ajoute la trace du F1 score
    fig.add_trace(go.Scatter(x=df['Levels'], y=df['F1 Score'], mode='lines+markers', name='F1 Score',
                             text=df['F1 Score'], hovertemplate='Level: %{x}<br>F1 Score: %{y:.2f}'))
    
    # On ajoute la trace de la Précision
    fig.add_trace(go.Scatter(x=df['Levels'], y=df['Precision'], mode='lines+markers', name='Precision',
                             text=df['Precision'], hovertemplate='Level: %{x}<br>Precision: %{y:.2f}'))
    
    # On ajoute la trace du Rappel
    fig.add_trace(go.Scatter(x=df['Levels'], y=df['Recall'], mode='lines+markers', name='Recall',
                             text=df['Recall'], hovertemplate='Level: %{x}<br>Recall: %{y:.2f}'))
    
    # On met à jour la mise en page pour une meilleure visualisation
    fig.update_layout(title='Evolution of F1 Score, Precision, and Recall with Additional Levels',
                      xaxis_title='Levels',
                      yaxis_title='Scores',
                      yaxis=dict(range=[0, 1]),
                      template='plotly_white')
    
    # On affiche le graphique interactif
    fig.show()

    # On enregistre le graphique en tant que fichier HTML
    pio.write_html(fig, file='scores_evolution.html', auto_open=False)

In [130]:
evaluate_model_multi_label(test)

+----------+-----------+--------+----------+
|  Level   | Precision | Recall | F1 Score |
+----------+-----------+--------+----------+
| Section  |    0.85   |  1.0   |   0.92   |
|  Class   |    0.75   |  0.9   |   0.82   |
| Subclass |    0.71   |  0.73  |   0.72   |
|  Group   |    0.67   |  0.58  |   0.62   |
| Subgroup |    0.65   |  0.46  |   0.54   |
+----------+-----------+--------+----------+
